In [1]:
import numpy as np
import matplotlib.pyplot as plt
%matplotlib notebook
plt.style.use('ggplot')
import random
from random import randint
import math

# System Parameters

In [2]:
food_amount = 100
pacman_amount = 1
board_size = 100
default_health = 5
pacmen = []
food = []
crot = 1
cloc =.2
cbite = 1
turn_loss = 1
phi_prec = (80/255.)
alpha_prec = 10/255.
delta_prec = 10/255.
pacman_radius = 1
food_health = 5

In [3]:
class pacman:
    def __init__(self):
        #change dynamically
        self.x = randint(0,board_size)
        self.y = randint(0,board_size)
        self.theta = randint(0,359)
        self.health = default_health
        #dna
        self.phi = randint(0,255)
        self.alpha = randint(0,255)
        self.delta = randint(0,255)
        
        self.phi_val = self.phi*phi_prec
        self.alpha_val = self.alpha*alpha_prec
        self.delta_val = self.delta*delta_prec
        #self.f = closest food
        #self.dist = closest food distance
    def __bool__(self):
        return True
    
    def __repr__(self):
        return "{pacman, x:"+str(self.x)+", y:"+str(self.y)+", phi:"+str(self.phi)+"}"
    
    def find_dist(self,f):
        return np.sqrt((self.x-f.x)**2 + (self.y-f.y)**2)
    
    def find_angle(self,f):
        dx = f.x - self.x
        dy = f.y - self.y
        theta1 = 360. - self.theta - math.degrees(math.atan((dx/dy)))
        theta2 = 360. - self.theta - theta1
        print(theta1)
        if(theta1 < theta2):
            return theta1
        return theta2
    
    def check_angle(self,f):#check if the food is in the range
        left_bound = self.theta - (self.phi_val/2)
        right_bound = self.theta + (self.phi_val/2)
        f_angle = self.find_angle(f)
        if(left_bound > f_angle and right_bound < f_angle):
            return True
        if(left_bound > f_angle + 360. and right_bound < f_angle + 360.):
            return True
        return False
        
    def find_food(self):
        global food
        closest = False
        closest_dist = False
        for i in food:
            dist = self.find_dist(i)
            if((dist < closest_dist or not closest_dist) and (self.check_angle(i)) or True):
                closest = i
                closest_dist = dist
            self.f = closest
            self.dist = closest_dist
        if(closest != False):
            return True
        return False
        
    def rotate_to_food(self):
        #cost of rotate = crot*theta*health
        #no cost to rotation
        new_theta = self.find_angle(self.f)
        error = random.uniform(self.alpha_val/-2., self.alpha_val/2.)
        self.theta = new_theta + error
        
    def get_food(self):
        self.rotate_to_food()
        error = random.uniform(self.delta_val/-2., self.delta_val/2.)
        new_dist = self.dist + error
        angle = self.find_angle(self.f)
        self.x += new_dist*np.cos(angle)
        self.x = 400
        self.y += new_dist*np.sin(angle)
        cost = cloc*new_dist
        self.health -= cost
        #cost of rotate
    
    def bite(self):
        to_food = self.find_dist(self.f)
        self.health -= cbite
        if(to_food < pacman_radius):#means the bite was sucessful
            self.health += food_health
            food.remove(self.f)
            
    
    def random_rotate(self):
        self.theta = randint(0,359)
        #self.health += randint(-2,1)
    
    def step(self):
        self.health -= turn_loss
        if(self.find_food()):
            self.get_food()
            self.bite()
        self.random_rotate()
    
    
    def get_genes(self):
        return[self.phi,self.alpha,self.delta]
    
    def set_genes(self,genes):
        self.phi = genes[0]
        self.alpha = genes[1]
        self.delta = genes[2]
        
    def to_bits(self):
        genes = self.get_genes()
        split_genes = []
        for i in genes:
            bin_str = format(i, '#010b')
            bin_str = bin_str[2:]
            split_genes.append([bin_str[:4],bin_str[4:]])
        return split_genes
    
    def reproduce(self,other):
        son1 = pacman()
        son2 = pacman()
        son1_genes = []
        son2_genes = []
        mybits = self.to_bits()
        otherbits = other.to_bits()
        for i,v in enumerate(mybits):
            son1_gene = v[0]+otherbits[i][1]
            son2_gene = otherbits[i][0]+v[1]
            son1_gene = int('0b'+son1_gene,base=2)
            son2_gene = int('0b'+son2_gene,base=2)
            son1_genes.append(son1_gene)
            son2_genes.append(son2_gene)
        son1.set_genes(son1_genes)
        son2.set_genes(son2_genes)
        return [son1,son2]
        
        
p = pacman()
p2 = pacman()
print(p.reproduce(p2))

[{pacman, x:86, y:89, phi:181}, {pacman, x:67, y:66, phi:55}]


In [4]:
class dot:
    def __init__(self):
        self.x = random.uniform(0, board_size)
        self.y = random.uniform(0, board_size)
    def __repr__(self):
        return "{dot, x:"+str(self.x)+", y:"+str(self.y)+"}"

In [5]:
def gen1():
    global pacmen
    pacmen = []
    for i in range(0,pacman_amount):
        p = pacman()
        pacmen.append(p)
    pacmen = np.array(pacmen)
    print(pacmen[0])
    return pacmen

def food1():
    global food
    food = []
    for i in range(0,food_amount):
        f = dot()
        food.append(f)
    food = np.array(food)
    return food

In [6]:
def driver(gen,life_span,generations):
    food = food1()
    dt = 1
    t = [0]
    tracker = []
    global pacmen
        
    for g in range(0,generations): #iterates through each generation
        tracker.append([])
        for i in range(0,len(pacmen)):
            tracker[g].append([])
        t.append(t[-1]+dt)
        for q in range(0,life_span): #runs through time with current generation
            for i,v in enumerate(pacmen):
                tracker[g][i].append([v.x,v.y,v.theta])
                v.step()
        
        
        #makes the next generation
        sons = []
        healthy_pacmen = []
        for i,v in enumerate(pacmen): #end of a generation mean reproduce
                if(v.health > 0):
                    healthy_pacmen.append(v)
        
        for i,v in enumerate(healthy_pacmen):
            if( i % 2 == 1):
                temp = v.reproduce(healthy_pacmen[i-1])
                sons.extend(temp)
                
        #print('generation over')
        pacmen = sons
    return t,tracker

In [9]:
t,tracker = driver(gen1(),10,1)
#print(tracker[0][0])

{pacman, x:67, y:77, phi:52}
263.5206654046971
280.90858284436945
289.3060238383546
312.58911836807846
318.2527553136118
357.59514264881625
231.35988590048692
190.56070476453618
239.54516887866865
262.2616401859034
216.8928508215002
256.6469532539659
193.3660130014478
365.5313742190705
194.6486339429472
217.30004675424482
211.63534195247934
361.9547070477688
214.01428330165984
216.15385559839225
344.95091764643075
366.4132067446574
345.116386932689
316.7710592544355
264.3461994582524
223.3033829633468
226.58295610986514
319.4434441299796
213.68655639652883
187.89796729366674
276.0546321730351
249.9774657754155
227.7628736564204
363.87603056380107
191.02775957234925
252.38192422629947
345.7424466526589
189.5200494315498
254.31958705513284
206.42781962516605
317.1173237398926
244.5725232222342
204.9130362276265
311.281630855251
220.22523980843175
235.00767008839676
338.4154956705046
296.3382940675976
397.9422421075771
7.68378126140378
6.909672635589189
7.696185140659253
8.495919048943009